In [1]:
import matplotlib.pyplot as plt
import plotly.plotly as py
import plotly.graph_objs as go
import numpy as np
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
config={'showLink': False, 'displayModeBar': False}

init_notebook_mode(connected=True)

from IPython.core.display import display, HTML
display(HTML(
    '<script>'
        'var waitForPlotly = setInterval( function() {'
            'if( typeof(window.Plotly) !== "undefined" ){'
                'MathJax.Hub.Config({ SVG: { font: "STIX-Web" }, displayAlign: "center" });'
                'MathJax.Hub.Queue(["setRenderer", MathJax.Hub, "SVG"]);'
                'clearInterval(waitForPlotly);'
            '}}, 250 );'
    '</script>'
))

display(HTML(
    '<style type="text/css">'
    '.plotly-graph-div {'
        'display: block;'
        'margin-left: auto;'
        'margin-right: auto;'
    '}'
    '</style>'
))


<center><h1 style="font-family:timesnewroman;font-size:40px">T<sub>1</sub> Mapping: Inversion Recovery</h1></center>
<p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Widely considered the gold standard for T1 mapping, the inversion recovery technique estimates T1 values by fitting the signal recovery curve acquired at different delays after an inversion pulse (180°). In a typical inversion recovery experiment (Figure 1), magnetization at thermal equilibrium is inverted using a 180° RF pulse. After the longitudinal magnetization recovers through spin-lattice relaxation for predetermined delay (“inversion time”, TI), a 90° excitation pulse is applied, followed by a readout imaging sequence (typically a spin-echo or gradient-echo readout) to create a snapshot of the longitudinal magnetization state at that TI. Inversion recovery was first developed for NMR in the 1940s (Hahn 1949, Drain 1949), and the first T1 map was acquired using a saturation-recovery technique (90° as a preparation pulse instead of 180°) by Pykett and Mansfield in 1978. Some distinct advantages of inversion recovery is its large potential range of signal change (up to 2M0) and an insensitivity to pulse sequence parameter imperfections (Stikov 2015). Despite its proven robustness at measuring T1, inversion recovery is scarcely used in practice, because conventional implementations requires repetition times (TRs) on the order of 2 to 5 T1 (Steen 1994), making it challenging to acquire whole-organ T1 maps in a clinically feasible time. Nonetheless, it is continuously used as a reference measurement during the development of new techniques or when comparing different T1 mapping techniques, and several variations of the inversion recovery technique have been developed that has made it practical for some applications.
</p>


<center>
<pstyle="line-height:1;font-family:timesnewroman;font-size:12px;>
<b>
Figure 1. Pulse sequence of an inversion recovery experiment.
</b>
</p>
</center>
         
<p>

<center><img src="ir_pulsesequences.png" style="width:640px;height:auto;"></center>

<center> <h2 style="font-family:timesnewroman;font-size:30px">Signal Modelling</h2> </center>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
The steady-state longitudinal magnetization of an inversion recovery experiment can be solved from the Bloch equations for the pulse sequence {θ180 – TI – θ90 – (TR-TI)}(assuming a gradient echo readout), and is given by:
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px;margin-top:60px;margin-bottom:60px;">
<b>
$$M_z(TI) =  M_0\frac{1-\cos(\theta_{180})e^{-\frac{TR}{T_1}}-[1-\cos(\theta_{180})]e^{-\frac{TI}{T_1}}}{1-\cos(\theta_{180})\cos(\theta_{90})e^{-\frac{TR}{T_1}}} \mathbf{\tag{1}} $$
</b>
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
where Mzis the longitudinal magnetization prior to the θ90. The real signal can be calculated from Eq. 1 by multiplying it by a factor of k·sin(θ90)·exp(-TE/T2), where k is a signal constant. This equation can be simplified by grouping together the constants for each measurements (at each TI, same TE and θ90 are used) and assuming ideal inversion pulses:
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px;margin-top:60px;margin-bottom:60px;">
<b>
$$M_z(TI) =  C(1-2e^{-\frac{TI}{T_1}}+e^{-\frac{TR}{T_1}})  \mathbf{\tag{2}} $$
</b>
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
where the first three terms and the denominator of equation (1) have been grouped together into the constant C. Furthermore, Eq. 2 can be further simplified if a long TR is use (TR > 5T1), which also benefits the SNR as 99% of the magnetization is recovered under this condition, allowing the last term in of Eq. 2 to be dropped:
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px;margin-top:60px;margin-bottom:60px;">
<b>
$$M_z(TI) =  C(1-2e^{-\frac{TI}{T_1}}) \mathbf{\tag{3}}$$
</b>
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
The simplicity of Eq. 3 (under appropriate experimental assumptions) has made it the most widely used to describe the signal evolution in an inversion recovery T1 mapping experiment. The magnetization curves are plotted in Figure 2 for near T1 values of three different tissues in the brain.
</p>

In [2]:
cd ../qMRLab
startup

    startup at line 1 column 1
    startup at line 1 column 1
loading struct
loading io
loading statistics
loading optim
loading image


In [3]:
%% Setup parameters
% All times are in seconds
% All flip angles are in degrees

params.TR = 5.0;
params.TI = linspace(0.001, params.TR, 1000);
            
params.TE = 0.004;
params.T2 = 0.040;
            
params.EXC_FA = 90;
params.INV_FA = 180;

params.signalConstant = 1;

In [4]:
%% Calculate signals
%

% White matter
params.T1 = 0.900;
signal_WM = inversion_recovery.analytical_solution(params, 'GRE-IR', 4);

% Grey matter
params.T1 = 1.500;
signal_GM = inversion_recovery.analytical_solution(params, 'GRE-IR', 4);

% CSF
params.T1 = 4.000;
signal_CSF = inversion_recovery.analytical_solution(params, 'GRE-IR', 4);

In [5]:
%get params --from Octave
%get signal_WM --from Octave
%get signal_GM --from Octave
%get signal_CSF --from Octave

<center>
<b>
Figure 2. Inversion recovery curves for three different T1 values of the main tissues of the brain.
</b>
</center>  
<p></p>

In [6]:
init_notebook_mode(connected=True)
# The polling here is to ensure that plotly.js has already been loaded before
# setting display alignment in order to avoid a race condition.

wm = go.Scatter(
    x = params["TI"],
    y = signal_WM,
    name = 'T<sub>1</sub> = 0.9 s (White Matter)'
)

gm = go.Scatter(
    x = params["TI"],
    y = signal_GM,
    name = 'T<sub>1</sub> = 1.5 s (Grey Matter)'
)

csf = go.Scatter(
    x = params["TI"],
    y = signal_CSF,
    name = 'T<sub>1</sub> = 4.0 s (Cerebrospinal Fluid)'
)

data = [wm, gm, csf]

layout = go.Layout(
    title='test',
    width=700,
    height=400,
    margin=go.layout.Margin(
        l=150,
        r=5,
        b=75,
        t=0,
    ),
    annotations=[
        dict(
            x=0.5004254919715793,
            y=-0.16191064079952971,
            showarrow=False,
            text='Inversion Time – TI (ms)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            xref='paper',
            yref='paper'
        ),
        dict(
            x=-0.15,
            y=0.4714285714285711,
            showarrow=False,
            text='Long. Magnetization (M<sub>z</sub>)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            textangle=-90,
            xref='paper',
            yref='paper'
        ),
    ],
    xaxis=dict(
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    yaxis=dict(
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    legend=dict(
        x=0.6,
        y=0.2,
        traceorder='normal',
        font=dict(
            family='Times New Roman',
            size=12,
            color='#000'
        ),
        bordercolor='#000000',
        borderwidth=2
    )
)

fig = dict(data=data, layout=layout)

iplot(fig, filename = 'basic-line', config = config)


<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Practically, Eq. 1 is the better choice for simulating the signal from an inversion recovery experiment, as the TRs are often chosen to be greater than 5*T1 of the tissue-of-interest, which rarely coincides with the longest T1 present (e.g. TR optimized for white matter, even though CSF is present in volume). In addition, Eq. 3 assumes ideal inversion pulses, which is rarely the case due to slice profile effects. Figure 3 displays the inversion recovery signal magnitude (normalized to 1) of a sample with a T1 = 3.0 s and a TR = 5 s calculated using both equations.
<p/>

<center>
<b>
Figure 3. Signal recovery curve simulated using Eq. 3 (solid) and Eq. 1 (dotted) for T1 = 3 s and TR = 5 s.
</b>
</center>
<p></p>

In [7]:
clear T1range
T1range = 0.25:0.25:5;
for ii = 1:length(T1range)
    params.T1 = T1range(ii);
    
    signal_T1_Eq1{ii} = inversion_recovery.analytical_solution(params, 'GRE-IR', 1);

    signal_T1_Eq3{ii} = inversion_recovery.analytical_solution(params, 'GRE-IR', 4);
end


In [8]:
%get T1range --from Octave
%get signal_T1_Eq1 --from Octave
%get signal_T1_Eq3 --from Octave

In [9]:
init_notebook_mode(connected=True)

data1 = [dict(
        visible = False,
        x = params["TI"],
        y = abs(signal_T1_Eq3[ii]),
        name = '[Eq. 3] – Long TR approximation') for ii in range(len(T1range))]

data1[3]['visible'] = True

data2 = [dict(
        visible = False,
        x = params["TI"],
        y = abs(signal_T1_Eq1[ii]),
        line = dict(
            color = ('rgb(22, 96, 167)'),
            dash = 'dash'),
        name = '[Eq. 1] – General Equation') for ii in range(len(T1range))]

data2[3]['visible'] = True

data = data1 + data2

steps = []
for i in range(len(T1range)):
    step = dict(
        method = 'restyle',  
        args = ['visible', [False] * len(data1)],
        label = str(T1range[i])
    )
    step['args'][1][i] = True # Toggle i'th trace to "visible"
    steps.append(step)

sliders = [dict(
    x = 0,
    y = -0.05,
    active = 3,
    currentvalue = {"prefix": "T1 value (s): "},
    pad = {"t": 50, "b": 10},
    steps = steps
)]

layout = go.Layout(
    width=700,
    height=450,
    margin=go.layout.Margin(
        l=150,
        r=5,
        b=85,
        t=10,
    ),
    annotations=[
        dict(
            x=0.5004254919715793,
            y=-0.16191064079952971,
            showarrow=False,
            text='Inversion Time – TI (ms)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            xref='paper',
            yref='paper'
        ),
        dict(
            x=-0.11,
            y=0.4714285714285711,
            showarrow=False,
            text='Signal (magnitude)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            textangle=-90,
            xref='paper',
            yref='paper'
        ),
    ],
    xaxis=dict(
        autorange=False,
        range=[0, 5],
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    yaxis=dict(
        autorange=False,
        range=[0, 1],
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    legend=dict(
        x=0.5,
        y=0.5,
        traceorder='normal',
        font=dict(
            family='Times New Roman',
            size=12,
            color='#000'
        ),
        bordercolor='#000000',
        borderwidth=2
    ), 
    sliders=sliders
)

fig = dict(data=data, layout=layout)

iplot(fig, filename = 'basic-line', config = config)

<center> <h2 style="font-family:timesnewroman;font-size:30px">Data Fitting</h2> </center>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Several factors impact the choice inversion recovery fitting algorithm.  If only magnitude images are available, then a polarity-inversion is often implemented to restore the non-exponential magnitude curves (Figure 3) into the exponential form (Figure 2). This process is sensitive to noise due to the noise creating a non-zero level at the signal null, and the spacing of the TIs of the acquired data. If phase data is also available, then a phase term must be added to the fitting equation (Barral 2010). Equation 3 must only be used to fit data for the long TR regime (TR > 5*T1), which in practice is rarely satisfied for all tissues in subjects.
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Early implementations of inversion recovery fitting algorithms were designed around the computational power available at the time. These included the “null method” (Pykett 1983), assuming that each T1 values have unique zero-crossings (see Figure 2), and linear fitting a rearranged version of Eq. 3 on a semi-log plot (Fukushima 1981). Nowadays, a non-linear least-squares fitting algorithm (e.g. Levenberg-Marquardt) is more appropriate, and can be applied to either approximate or general forms  of the signal model (Eq. 3 vs Eq. 1). More recent work by Barral et al (Barral 2010) demonstrated that T1 maps can also be fitted much quicker (x75) than simply using Levenberg-Marquardt to fit  Eq. 1 – without a precision penalty – by using a reduced-dimension non-linear least squares (RD-NLS) algorithm. It was demonstrated that the following simplified 5-parameter equation can be sufficient for accurate T1 mapping:
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px;margin-top:60px;margin-bottom:60px;">
<b>
$$S(TI) =  a+be^{-\frac{TI}{T_1}} \mathbf{\tag{4}}$$
</b>
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
where a and b are complex values. If magnitude-only data is available, a 3-parameter model can be sufficient by taking the absolute value of Eq. 4.  While the RD-NLS algorithms are too complex to be presented here (the reader is referred to the paper, Barral 2010),  the code for these algorithms were released open-source along with the original publication (http://www-mrsrl.stanford.edu/~jbarral/t1map.html), and are also available as a qMRLab T1 mapping model (https://github.com/neuropoly/qMRLab). One important thing to note about Eq. 4 is that they are general – no assumptions is made about TR – and thus are as robust as Eq. 1 as long as all pulse sequence parameters other than TI are kept constant between each measurements. Figure 4 compares simulated data (Eq. 1) using a range of TRs (1.5·T1 to 5·T1) fitted using either RD-NLS & Eq. 4 or a Levenberg-Marquardt fit of Eq. 2.
</p>

<center style="margin-left:60px;margin-right:60px">
<b>
Figure 4. Fitting comparison of simulated data (blue markers) with T<sub>1</sub> = 1 s and TR = 1.5 to 5 s, using fitted using RD-NLS & Eq. 4 (orange) and Levenberg-Marquadt & Eq. 2 (long TR approximation).
</b>
</center>
<p></p>

In [10]:
params.EXC_FA = 90;
params.INV_FA = 180;
params.TI = 50:50:1500;
params.T1 = 1000;
TR = 1500:50:5000;

for ii = 1:length(TR)
    params.TR = TR(ii);
    Mz_analytical(ii,:) = inversion_recovery.analytical_solution(params, 'GRE-IR', 1);
end

TI = params.TI;


x0(1) = 0.5;
x0(2) = 900;
options.Algorithm = 'levenberg-marquardt';

for ii=1:length(TR)
    y = abs(Mz_analytical(ii,:));
    fun = @(x) abs(x(1) .* (1 - 2.*exp(-TI./x(2)))) - y;

    [fitOutput_nlsq(ii,:), resnorm] = lsqnonlin(fun,x0,[],[],options);
    T1_nlsq(ii) = fitOutput_nlsq(ii,2);
end


irObj = inversion_recovery();
irObj.Prot.IRData.Mat = params.TI';

for ii=1:length(TR)

    data.IRData = Mz_analytical(ii,:);

    fitOutput_barral{ii} = irObj.fit(data);

    T1_barral(ii) = fitOutput_barral{ii}.T1;

end

In [11]:
%get params --from Octave
%get Mz_analytical --from Octave
%get fitOutput_nlsq --from Octave
%get fitOutput_barral --from Octave
%get TR --from Octave

In [12]:
init_notebook_mode(connected=True)

data1 = [dict(
        visible = False,
        mode = 'markers',
        x = params["TI"],
        y = abs(np.squeeze(np.asarray(Mz_analytical[ii]))),
        name = 'Simulated data') for ii in range(len(TR))]

data1[10]['visible'] = True

data2 = [dict(
        visible = False,
        mode = 'lines',
        x = params["TI"],
        y = abs(fitOutput_nlsq[ii,0] * (1 - 2*np.exp(-params['TI']/fitOutput_nlsq[ii,1]))),
        name = 'Fitted T1 [C(1-2*exp(-TI/T1))]:' + str(round(fitOutput_nlsq[ii,1])) + ' ms') for ii in range(len(TR))]

data2[10]['visible'] = True

data3 = [dict(
        visible = False,
        mode = 'lines',
        x = params["TI"],
        y = abs((fitOutput_barral[ii]['ra']+fitOutput_barral[ii]['rb']*np.exp(-params['TI']/fitOutput_barral[ii]['T1']))),
        name = 'Fitted T1 [ra+rb*exp(-TI/T1)]:' + str(round(fitOutput_barral[ii]['T1'])) + ' ms') for ii in range(len(TR))]

data3[10]['visible'] = True



data = data1 + data2 + data3

steps = []
for i in range(len(TR)):
    step = dict(
        method = 'restyle',  
        args = ['visible', [False] * len(data1)],
        label = str(TR[i])
        )
    step['args'][1][i] = True # Toggle i'th trace to "visible"
    steps.append(step)

sliders = [dict(
    x = 0,
    y = -0.05,
    active = 10,
    currentvalue = {"prefix": "TR value (ms): "},
    pad = {"t": 50, "b": 10},
    steps = steps
)]

layout = go.Layout(
    width=700,
    height=500,
    margin=go.layout.Margin(
        l=150,
        r=5,
        b=85,
        t=10,
    ),
    annotations=[
        dict(
            x=0.5004254919715793,
            y=-0.16191064079952971,
            showarrow=False,
            text='Inversion Time – TI (ms)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            xref='paper',
            yref='paper'
        ),
        dict(
            x=-0.11,
            y=0.4714285714285711,
            showarrow=False,
            text='Signal (magnitude)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            textangle=-90,
            xref='paper',
            yref='paper'
        ),
    ],
    xaxis=dict(
        autorange=False,
        range=[0, params['TI'][-1]],
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    yaxis=dict(
        autorange=False,
        range=[0, 1],
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    legend=dict(
        x=0.4,
        y=0.9,
        traceorder='normal',
        font=dict(
            family='Times New Roman',
            size=12,
            color='#000'
        ),
        bordercolor='#000000',
        borderwidth=2
    ), 
    sliders=sliders
)

fig = dict(data=data, layout=layout)

iplot(fig, filename = 'basic-line', config = config)

<center> <h2 style="font-family:timesnewroman;font-size:30px">Benefits and Pitfalls</h2> </center>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
The conventional inversion recovery experiment (long TR values and a sufficient number of inversion times (typically 5 or more) covering the range [0, TR]) is considered the gold standard T1 mapping technique due to methodological characteristics. It offers a wide dynamic range of signals ([-kM0, kM0] for very long TRs), meaning a wide range of TI value acquisitions where high SNR is available to sample the signal recovery curve (Fukushima 1981). Due all parameters except TI being constant for each measurement and that only a single acquisition is performed (at TI) for each TR, T1 maps produced by inversion recovery are largely insensitive to inaccuracies in excitation flip angles and imperfect spoiling (Stikov 2015), and unless Eq. 3 is used as the model, it does not assume perfect inversion pulses (Barral 2010). Inversion recovery can also often be acquired using commonly available standard pulse sequences available on most MRI scanners by setting up a customized acquisition protocol, and does not require any additional calibration measurements like a B1 map.
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Despite its widely acknowledged robustness at measuring accurate T1 maps, inversion recovery is no longer widely used in practice for studies. The main drawback of this technique is the requirement for fairly long TR values, on the order of T1 for general models (e.g. Eqs. 1, 4, and 5), and up to 5*T1 for the historically most used model (Eq. 3). As only one TI is acquired per TR (unless variations are used, see next sections), and conventional cartesian gradient readout imaging acquires one phase encode line per excitation,  if T1 values of tissues of interest are in the range of 1-2 seconds, it takes about to 10-25 minutes to acquire a single-slice T1 map using the inversion recovery technique, making it impossible to acquire whole-organ T1 maps in clinically feasible protocol times. Nonetheless, the strength of inversion recovery , and it is still useful as a reference measurement when comparing against other T1 mapping methods, or to acquire a single-slice T1 map of a tissue prior to another experiment to optimize other pulse sequences for the T1 value-of-interest to be measured.
</p>


<center>
<b>
Figure 5. Lorem Ipsum.  Lorem Ipsum.  Lorem Ipsum.  Lorem Ipsum.  Lorem Ipsum.  Lorem Ipsum.  Lorem Ipsum.  Lorem Ipsum. 
</b>
</center>
<p></p>

In [13]:
TRrange = 1000:100:5000;


Model = inversion_recovery; 

x = struct;
x.T1 = 900;

Opt.SNR = 25;
Opt.M0 = 1;
Opt.FAinv = 180;
Opt.FAexcite = 90;

for ii = 1:length(TRrange)
    Opt.TR = TRrange(ii);
    Opt.T1 = x.T1;
    TI = linspace(0.05, Opt.TR, 6)';
    Model.Prot.IRData.Mat = [TI];
    [ra,rb] = Model.ComputeRaRb(x,Opt);
    x.rb = rb;
    x.ra = ra;
    for jj = 1:1000
        [FitResult{ii,jj}, noisyData{ii,jj}] = Model.Sim_Single_Voxel_Curve(x,Opt,0); 
        fittedT1(ii,jj) = FitResult{ii,jj}.T1;
        noisyData_array(ii,jj,:) = noisyData{ii,jj}.IRData;
    end
        
    for kk=1:length(TI)
        meanData(ii,kk) = mean(noisyData_array(ii,:,kk));
        stdData(ii,kk) = std(noisyData_array(ii,:,kk));
    end
    
    disp(Opt.TR)
    meanT1(ii) = mean(fittedT1(ii,:));
    stdT1(ii) = std(fittedT1(ii,:));
end


 1000
 1100
 1200
 1300
 1400
 1500
 1600
 1700
 1800
 1900
 2000
 2100
 2200
 2300
 2400
 2500
 2600
 2700
 2800
 2900
 3000
 3100
 3200
 3300
 3400
 3500
 3600
 3700
 3800
 3900
 4000
 4100
 4200
 4300
 4400
 4500
 4600
 4700
 4800
 4900
 5000


In [14]:
clear dataTI
for ii = 1:length(TRrange)
    dataTI(ii,:) = linspace(0.05, TRrange(ii), 6);
end

clear dataTI_long
clear noiselessData

for ii = 1:length(TRrange)
    dataTI_long(ii,:) = linspace(0.05, TRrange(ii), 500);
    Model.Prot.IRData.Mat = [dataTI_long(ii,:)];
    Opt.TR = TRrange(ii);
    Opt.T1 = x.T1;
    [ra,rb] = Model.ComputeRaRb(x,Opt);
    x.rb = rb;
    x.ra = ra;

    noiselessData(ii,:) = Model.equation(x);
end

In [15]:
%get TRrange --from Octave
%get meanData --from Octave
%get stdData --from Octave
%get meanT1 --from Octave
%get stdT1 --from Octave
%get dataTI --from Octave
%get dataTI_long --from Octave
%get noiselessData --from Octave

In [16]:
init_notebook_mode(connected=True)

data1 = [dict(
        visible = False,
        x = np.squeeze(np.asarray(dataTI[ii,:])),
        y = np.squeeze(np.asarray(meanData[ii,:])),
        error_y=dict(
            type='data',
            color = ('rgb(22, 96, 167)'),
            array=np.squeeze(np.asarray(stdData[ii,:])),
            visible=True
        ),
        line = dict(
            color = ('rgb(22, 96, 167)'),
            dash = 'dot'),
        mode = 'markers',
        name = 'Monte Carlo simulated signal') for ii in range(len(TRrange))]

data1[28]['visible'] = True

data2 = [dict(
        visible = False,
        x = np.squeeze(np.asarray(dataTI_long[ii,:])),
        y = np.squeeze(np.asarray(noiselessData[ii,:])),
        line = dict(
            color = ('rgb(247, 152, 19)'),
            ),
        name = 'Noiseless signal') for ii in range(len(TRrange))]

data2[28]['visible'] = True

data_meanT1 = [dict(
    visible = False,
    x = TRrange,
    y = meanT1,
    name = 'Mean T<sub>1</sub> (s)',
    xaxis='x2',
    yaxis='y2') for ii in range(len(TRrange))]
data_meanT1[15]['visible'] = True

data_stdT1 = [dict(
    visible = False,
    x = TRrange,
    y = stdT1,
    name = 'STD T<sub>1</sub> (s)',
    xaxis='x2',
    yaxis='y3') for ii in range(len(TRrange))]

data_stdT1[28]['visible'] = True

data = data2 + data1 + data_meanT1 + data_stdT1

steps = []
for i in range(len(TRrange)):
    step = dict(
        method = 'restyle',  
        args = ['visible', [False] * len(data1)],
        label = str(TRrange[i])
    )
    step['args'][1][i] = True # Toggle i'th trace to "visible"
    steps.append(step)

sliders = [dict(
    x = 0,
    y = -0.02,
    active = 28,
    currentvalue = {"prefix": "TR value (ms): "},
    pad = {"t": 50, "b": 10},
    steps = steps
)]

layout = go.Layout(
    margin=go.layout.Margin(
        l=150,
        r=5,
        b=100,
        t=10,
        pad=0
    ),
    annotations=[
        dict(
            x=0.5004254919715793,
            y=-0.16191064079952971,
            showarrow=False,
            text='Inversion Time – TI (ms)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            xref='paper',
            yref='paper'
        ),
        dict(
            x=-0.11,
            y=0.4714285714285711,
            showarrow=False,
            text='Signal (magnitude)',
            font=dict(
                family='Times New Roman',
                size=26
            ),
            textangle=-90,
            xref='paper',
            yref='paper'
        ),
        dict(
            x=0.75,
            y=0.75,
            showarrow=False,
            text='<b>TR (ms)<b>',
            font=dict(
                family='Times New Roman',
                size=14
            ),
            xref='paper',
            yref='paper'
        ),
        dict(
            x=0.43,
            y=0.35,
            showarrow=False,
            text='<b>Mean T<sub>1</sub> (ms)<b>',
            font=dict(
                family='Times New Roman',
                size=14
            ),
            textangle=-90,
            xref='paper',
            yref='paper'
        ),
        dict(
            x=0.98,
            y=0.35,
            showarrow=False,
            text='<b>STD T<sub>1</sub> (ms)<b>',
            font=dict(
                family='Times New Roman',
                size=14
            ),
            textangle=-90,
            xref='paper',
            yref='paper'
        )
    ],
    xaxis=dict(
        autorange=False,
        range=[0, 5000],
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    yaxis=dict(
        autorange=False,
        range=[0, 1],
        showgrid=False,
        linecolor='black',
        linewidth=2
    ),
    xaxis2=dict(
        domain=[0.5, 0.90],
        anchor='y2',
        mirror = True,
        side='top',
        ticks='inside',
        showline=True,
    ),
    yaxis2=dict(
        autorange=False,
        range=[500, 1300],
        domain=[0.05, 0.65],
        anchor='x2',
        mirror = True,
        ticks='inside',
        showline=True,
    ),
    yaxis3=dict(
        autorange=False,
        range=[0, 190],
        domain=[0.05, 0.65],
        anchor='x2',
        overlaying='y2',
        side='right',
        ticks='inside',
    ),
    legend=dict(
        x=1.02,
        y=1,
        traceorder='normal',
        font=dict(
            family='Times New Roman',
            size=12,
            color='#000'
        ),
        bordercolor='#000000',
        borderwidth=2
    ), 
    sliders=sliders
)

fig = dict(data=data, layout=layout)

iplot(fig, filename = 'basic-line', config = config)

<center> <h2 style="font-family:timesnewroman;font-size:30px">Other Saturation-Recovery T<sub>1</sub> Mapping techniques</h2> </center>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Several variations of the inversion recovery pulse sequence exist, developed to overcome some of the challenges specified above. Out of them, the Look-Locker technique may be the most widely used one. Instead of a single acquisition at time TI, a periodic train of small excitation pulses θ are applied after the inversion pulse, {θ180 – 𝛕 – θ – 𝛕 – θ – ...}, where  𝛕 = TR/n and n is the number of sampling acquisitions. This pulse sequence samples the relaxation curve much more efficiently which substantially reduces the acquisition time relative to inversion recovery, but at a cost of lower SNR. However, because the magnetization state of each TI measurement depends on the previous series of θ excitation, it has higher sensitivity to B1-inhomogeneities and imperfect spoiling than inversion recovery (Gai 2013, Stikov 2015). Nonetheless, Look-Locker is widely used for rapid T1 mapping applications, and variants like MOLLI (Modified Look-Locker Inversion recovery) has reached speeds allowing for cardiac applications (Messroghli 2014).
</p>

<p style="line-height:2;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Another inversion recovery variant that’s worth to mention is saturation recovery, in which the inversion pulse is replaced with a saturation pulse: {θ90 – TI – θ90}. This technique was used to acquire the very first T1 map (Pykett and Mansfield 1978). Unlike inversion recovery, this pulse sequence does not need a long TR to recover to its initial condition; every θ90 pulse resets the longitudinal magnetization to the same state as just after the first preparation θ90 pulse. However, to properly sample the recovery curve, TI’s still need to reach the order of ~T1, the dynamic range of available signal is cut in half ([0, M0]), and the short TIs have the lowest SNRs.
</p>

<center> <h2 style="font-family:timesnewroman;font-size:30px">Works Cited</h2> </center>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Barral, Joëlle K., et al. “A Robust Methodology for in Vivo T1 Mapping.” Magnetic Resonance in Medicine, vol. 64, no. 4, 2010, pp. 1057–1067., doi:10.1002/mrm.22497.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Drain, L E. “A Direct Method of Measuring Nuclear Spin-Lattice Relaxation Times.” Proceedings of the Physical Society. Section A, vol. 62, no. 5, Jan. 1949, pp. 301–306., doi:10.1088/0370-1298/62/5/306.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Gai, Neville D., et al. “Modified Look-LockerT1evaluation Using Bloch Simulations: Human and Phantom Validation.” Magnetic Resonance in Medicine, vol. 69, no. 2, 2012, pp. 329–336., doi:10.1002/mrm.24251.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Hahn, Erwin L. “An Accurate Nuclear Magnetic Resonance Method for Measuring Spin-Lattice Relaxation Times.” Physical Review, vol. 76, no. 1, Jan. 1949, pp. 145–146., doi:10.1103/physrev.76.145.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Messroghli, Daniel R., et al. “Modified Look-Locker Inversion Recovery (MOLLI) for High-resolutionT1 Mapping of the Heart.” Magnetic Resonance in Medicine, vol. 52, no. 1, 2004, pp. 141–146., doi:10.1002/mrm.20110.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Pykett, I L, et al. “Measurement of Spin-Lattice Relaxation Times in Nuclear Magnetic Resonance Imaging.” Physics in Medicine and Biology, vol. 28, no. 6, Jan. 1983, pp. 723–729., doi:10.1088/0031-9155/28/6/012.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Pykett, I L, and P Mansfield. “A Line Scan Image Study of a Tumorous Rat Leg by NMR.” Physics in Medicine and Biology, vol. 23, no. 5, Jan. 1978, pp. 961–967., doi:10.1088/0031-9155/23/5/012.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Steen, R. Grant, et al. “Precise and Accurate Measurement of Proton T1 in Human Brain in Vivo: Validation and Preliminary Clinical Application.” Journal of Magnetic Resonance Imaging, vol. 4, no. 5, 1994, pp. 681–691., doi:10.1002/jmri.1880040511.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Stikov, Nikola, et al. “On the Accuracy of T1mapping: Searching for Common Ground.” Magnetic Resonance in Medicine, vol. 73, no. 2, 2014, pp. 514–522., doi:10.1002/mrm.25135.
</p>

<p style="line-height:1.5;font-family:timesnewroman;font-size:18px;text-align:justify;margin-left:60px;margin-right:60px">
Weiss, Al. “E. Fukushima, St. B. W. Roeder: Experimental Pulse NMR. A Nuts and Bolts Approach. Addison-Wesley Publ. Comp., Inc., Reading, Massachusetts 1981. 539 Seiten, Preis: US $ 34.50.” Berichte Der Bunsengesellschaft Für Physikalische Chemie, vol. 87, no. 5, 1983, pp. 458–458., doi:10.1002/bbpc.19830870533.
</p>